In [ ]:
from scipy import constants
import numpy as np
import matplotlib.pyplot as plt
from numpy.linalg import inv

In [ ]:
hbarc = 197.327

'Boson mass in MeV'
Mass = (constants.value(u'proton mass energy equivalent in MeV') + constants.value(u'neutron mass energy equivalent in MeV'))*0.5

'2-body scattering length in MeV^-1'
a0 = 14.051/hbarc 

'Dimer binding energy in MeV'
DimerBindingEnergy = 1/(Mass*a0**2)

'Dimer binding momentum in MeV'
DimerBindingMomentum = np.sqrt(Mass*DimerBindingEnergy)

'For i*eps prescription'
epsilon = 10**(-8)

In [ ]:
def theta(p):
  """
  Calculates the angle for Hetherington Schick method for incoming dimer momentum p

  Parameters
  -----------
  p: float

  Returns
  -----------
  theta: float
  """
  return 0.5 * np.arctan(2*DimerBindingMomentum/p)

In [ ]:
def Legendre2(l, x):
  """
  Legendre function of the second kind

  Q_l(a) = 1/2 \int_{-1}^1  dx \frac{ P_l(x) }{ x+a }

  
  Parameters
  ----------
  l: int
  x: float or ndarray

  Returns
  -------
  float or ndarray
  """
  if l == 0:
    return 0.5 * np.log((x+1)/(x-1))
  else:
    raise ValueError('Legendre Polynomial of the Second Kind of order l not defined yet')

In [ ]:
def Energy(p):
  """
  Calculates energy in COM frame for momentum p
  """
  E = ((3 * p ** 2) / (4 * Mass)) - (DimerBindingMomentum ** 2 / Mass)
  return E




def DimerPropagator(p, E):
  return 1 / (np.sqrt(0.75 * p ** 2 - Mass * E - 1j * epsilon) - 1/a0)

In [ ]:
def Inhom(p, q):
  pass



def Kernel(k, p, q):
  a = (p ** 2 + q ** 2 - Mass * Energy(k) - 1j * epsilon) / (p * q)
  kernel = (2/np.pi) * q * DimerPropagator(q, Energy(k)) * Legendre2(0, a)/p
  return kernel

In [ ]:
def quadrature(lower_bound = 0, upper_bound = 100, points = 100, quadrature_method = 'linear'):
  """
  Calculates the points and weights for integration by quadrature

  Parameters
  ----------
  lower_bound: int
  upper_bound: int
  points: int
  quadrature_method: str

  Returns
  ---------
  q: ndarray
  weights: ndarray 
  """
  if quadrature_method == 'linear':
    q = np.linspace(lower_bound, upper_bound, points)
    weights = ((upper_bound - lower_bound) / (points - 1)) * np.ones(points)  
    return q, weights
  elif quadrature_method == 'Gaussian Quadrature':
    q = np.polynomial.legendre.leggauss(points)[0] * ((upper_bound - lower_bound) / 2) + ((upper_bound + lower_bound) / 2)
    weights = np.polynomial.legendre.leggauss(points)[1] * ((upper_bound - lower_bound) / 2)
    return q, weights
  else:
    raise ValueError('Quadrature type not supported')


def RealAxisSolution(k, quadrature_points, quadrature_weights):
  """
  Solves the inhomogeneous integral equation for a kernel with no poles or branch
  cuts on the real axis

  Parameters
  ----------
  k: ndarray
  quadrature_points: ndarray
  quadrature_weights: ndarray

  Return
  ---------
  amp: ndarray
  """
  pp, qq = np.meshgrid(k, quadrature_points, indexing='ij')
  KernelMat = Kernel(k, pp, qq)
  for j in range(len(quadrature_weights)):
    KernelMat[:, j] *= quadrature_weights[j]
  amp = np.dot(inv(np.eye(KernelMat.shape[0]) - KernelMat), Inhom(k, k))
  return amp

In [ ]:
def Hetherington_contour(p, points, weights):
        if theta(p) >= 0 and theta(p) < np.pi/2:
            line_bound_point = points[points <= np.cos(theta(p))*(upper_bound - lower_bound) + lower_bound]
            line_bound_weight = weights[:len(line_bound_point)]
            line_points = line_bound_point - 1j*np.tan(theta(p))*(line_bound_point - lower_bound)
            line_weights = (1 - 1j * np.tan(theta(p))) * line_bound_weight
            arc_input = points[points > np.cos(theta(p))*(upper_bound - lower_bound) + lower_bound]
            arc_points = lower_bound + (upper_bound - lower_bound) * np.exp(-1j * np.arccos( (arc_input - lower_bound)/(upper_bound - lower_bound)) )
            arc_weights = -1j * np.exp(-1j * np.arccos( (arc_input - lower_bound) / (upper_bound - lower_bound))) * weights[len(line_bound_point):]/(np.sin(np.arccos( (arc_input - lower_bound) / (upper_bound - lower_bound))))
            contour_points = np.concatenate((line_points, arc_points))
            contour_weights = np.concatenate((line_weights, arc_weights))
            return contour_points, contour_weights

        elif theta(p) == np.pi/2:
            line_points = lower_bound + -1j * (points - lower_bound)
            arc_points = lower_bound + (upper_bound - lower_bound) * np.exp(-1j * np.arccos( (points - lower_bound)/(upper_bound - lower_bound)) )
            contour_points = np.concatenate((line_points, arc_points))
            contour_weights = np.concatenate((line_weights, arc_weights))
            return contour_points, contour_weights


def Hetherington_kernel(k, points, weights):
  contour_points, contour_weights = Hetherington_contour(k, points, weights)
  pp_contour, qq_contour = np.meshgrid(contour_points, contour_points, indexing='ij')
  HK = Kernel(k, pp_contour, qq_contour) * contour_weights
  return HK

def Hetherington_amplitude_contour(k, points, weights):
  contour_points, contour_weights = Hetherington_contour(k, points, weights)
  HK = Hetherington_kernel(k, points, weights)
  return np.dot(inv(np.eye(HK.shape[0]) - HK), Inhom(k, contour_points))

def Hetherington_offshell_amplitude(k, p, points, weights):
  contour_points, contour_weights = Hetherington_contour(k, points, weights)
  contour_amp = Hetherington_amplitude_contour(k, points, weights)
  amp = Inhom(k, p) + np.dot(Kernel(k, p, contour_points) * contour_weights, contour_amp)
  return amp

def Hetherington_onshell_amplitude(k, points, weights):
  return Hetherington_offshell_amplitude(k, k, points, weights)

In [ ]:
def PhaseShift():
  pass